In [1]:
using Plots
default(legend = false)

Set up Lorenz attractor model, plotting functions, etc.

In [2]:
s = 10.;
b = 8/3.;
r = 28.;

mutable struct Lorenz
     x; y; z;
end

# start a random initial state for a Lorenz attractor
rLorenz() = Lorenz(50.0*rand()-25.,50.0*rand()-25.,50.0*rand())

function step!(a::Lorenz, dt)
    a.x+=dt*s*(a.y-a.x);
    a.y+=dt*(a.x*(r-a.z)-a.y);
    a.z+=dt*(a.x*a.y-b*a.z);
end

# convenience function to update entire array of Lorenz attractors
function step!(attractors::Array{Lorenz, 1}, dt)
    for i in 1:length(attractors)
        step!(attractors[i], dt);
    end
end

Base.copy(a::Lorenz)=Lorenz(a.x,a.y,a.z)

function sync!(attractors::Array{Lorenz,1},weights::Array{Float64,2}, rnd)
    # calculate new x-coordinates and impose them
    local xs=zeros(length(attractors));
    for i in 1:length(attractors)
        for j in 1:length(attractors)
            xs[i]+=weights[i,j]*attractors[j].x;
        end
        xs[i]/=sum(weights[i,:]);
        xs[i]+=2*rnd*(rand()-.5)
    end

    # update coordinates
    for i in 1:length(attractors)
        attractors[i].x=xs[i];
    end
end

# perturbation
function perturb!(a::Lorenz, magnitude)
    # let's perturb at fixed magnitude, but random direction
    # so x^2+y^2+z^2 = magnitude^2
    # TODO: this only perturbs t in the positive plane....
    dx2 = magnitude^2*rand()
    dy2 = (magnitude^2-dx2)*rand()
    dz2 = (magnitude^2 - dx2 - dy2)rand()
    a.x += sqrt(dx2)
    a.y += sqrt(dy2)
    a.z += sqrt(dz2)
end

function perturb!(attractors::Array{Lorenz, 1}, magnitude)
    for i in 1:length(attractors)
        perturb!(attractors[i], magnitude)
    end
end

perturb! (generic function with 2 methods)

In [3]:
# 3d plot of array of Lorenz attractors
function plotL(rec::Array{Lorenz, 1})
    x=[rec[i].x for i=1:length(rec)]
    y=[rec[i].y for i=1:length(rec)]
    z=[rec[i].z for i=1:length(rec)]
    plot3d(x, y, z)
end
function plotL(rec::Array{Array{Lorenz,1},1})
    x=[rec[i][1].x for i=1:length(rec)];
    y=[rec[i][1].y for i=1:length(rec)];
    z=[rec[i][1].z for i=1:length(rec)];
    p = plot3d(x, y, z, xlim=(-25,25), ylim=(-25,25), zlim=(0,50))
    for j=2:length(rec[1])
        x = [rec[i][j].x for i=1:length(rec)]
        y = y,[rec[i][j].y for i=1:length(rec)]
        z = z,[rec[i][j].z for i=1:length(rec)]
        plot3d!(p, x,y,z)  #, xlim=(-25,25), ylim=(-25,25), zlim=(0,50))
    end
    display(p)
end

# YZ plane plot of array of Lorenz attractors
function plotLyz(rec::Array{Array{Lorenz,1},1})
    y=[rec[i][1].y for i=1:length(rec)];
    z=[rec[i][1].z for i=1:length(rec)];
    for j=2:length(rec[1])
        y=hcat(y,[rec[i][j].y for i=1:length(rec)]);
        z=hcat(z,[rec[i][j].z for i=1:length(rec)]);
    end
    plot(y,z, xlim=(-25,25), ylim=(0,50),leg=false)
end
function distYZ(a::Lorenz,b::Lorenz)
    sqrt((a.y-b.y)^2+(a.z-b.z)^2)
end
function dist(a::Lorenz,b::Lorenz)
    sqrt((a.x-b.x)^2+(a.y-b.y)^2+(a.z-b.z)^2)
end# 3d plot of array of Lorenz attractors

dist (generic function with 1 method)

### Sync and perturb
We'll periodically sync, and at a lower frequency, perturb the states. The idea is we can rely on the exponential decay in error to detect if a node has stopped syncing.

In [37]:
n = 20
weights = zeros(n, n)  # initialize decentralized nodes
weights[:, 1] .= 1. # make everything sync to the first node only
noise = 0.
dt = 0.001
comms_time = 0.01  # sample time
N_s = floor(comms_time/dt)  # every how many time-steps do we synchronize?
perturb_time = 0.001
N_p = floor(perturb_time/dt)
perturbation = 0.001
sim_time = 15.0  # time to simulate
time = collect(range(0, stop=sim_time, step=dt))
network = Array{Lorenz, 1}();
for i=1:n
    push!(network, rLorenz());
end

# set up logging
record = Array{Array{Lorenz, 1}, 1}();

# simulate
for i=1:length(time)
    if i%N_s==0  # periodically synchronize
        sync!(network, weights, noise)
    end
    if i%N_p==0
        perturb!(network, perturbation)
    end
    step!(network, dt)
    push!(record, deepcopy(network))
end

# plot distances
# * note: once the error is very very small, you need to remove `yaxis=:log`, or it won't plot
p = plot(time, [dist(record[i][1],record[i][2]) for i=1:length(record)], yaxis=:log)
for j=3:n
    plot!(p, time, [dist(record[i][1],record[i][j]) for i=1:length(record)], yaxis=:log)
end
display(p)

Now let's drop sync on half of them, and see how quickly they de-sync

In [38]:


for i = 10:20
    weights[i, 1] = 0
    weights[i, i] = 1
end

sim_time = 15.0  # time to simulate
time = collect(range(0, stop=sim_time, step=dt))

# set up logging
record2 = Array{Array{Lorenz, 1}, 1}();

# simulate
for i=1:length(time)
    if i%N_s==0  # periodically synchronize
        sync!(network, weights, noise)
    end
    if i%N_p==0
        perturb!(network, perturbation)
    end
    step!(network, dt)
    push!(record2, deepcopy(network))
end

# plot distances
# * note: once the error is very very small, you need to remove `yaxis=:log`, or it won't plot
p = plot(time, [dist(record2[i][1],record2[i][2]) for i=1:length(record2)], yaxis=:log, color="blue")
for j=3:n
    if weights[j, 1] > 0
        col = "blue"
    else
        col = "red"
    end
    plot!(p, time, [dist(record2[i][1],record2[i][j]) for i=1:length(record2)], yaxis=:log, color=col)
end
display(p)